In [1]:
import os
import json
from dotenv import load_dotenv
from agents.deals import ScrapedDeal, DealSelection

In [2]:
load_dotenv(override=True)
api_key = os.getenv("GROQ_API_KEY")

In [3]:
from groq import Groq

groq_client = Groq(api_key=api_key)

In [4]:
deals = ScrapedDeal.fetch(show_progress=True)

  0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 5/5 [03:44<00:00, 44.86s/it]


In [5]:
len(deals)

50

In [6]:
deals[44].describe()

"Title: Craftsman Blow Gun Kit for $17 + free shipping w/ $35\nDetails: Bag this nice low as part of today's Daily Deals. It's currently listed at $25 on Amazon. Buy Now at Lowe's\nFeatures: \nURL: https://www.dealnews.com/Craftsman-Blow-Gun-Kit-for-17-free-shipping-w-35/21740415.html?iref=rss-c196"

In [7]:
system_prompt = """You identify and summarize the 5 most detailed deals from a list, by selecting deals that have the most detailed, high quality description and the most clear price.
Respond strictly in JSON with no explanation, using this format. You should provide the price as a number derived from the description. If the price of a deal isn't clear, do not include that deal in your response.
Most important is that you respond with the 5 deals that have the most detailed product description with price. It's not important to mention the terms of the deal; most important is a thorough description of the product.
Be careful with products that are described as "$XXX off" or "reduced by $XXX" - this isn't the actual price of the product. Only respond with products when you are highly confident about the price. 

{"deals": [
    {
        "product_description": "Your clearly expressed summary of the product in 4-5 sentences. Details of the item are much more important than why it's a good deal. Avoid mentioning discounts and coupons; focus on the item itself. There should be a paragpraph of text for each item you choose.",
        "price": 99.99,
        "url": "the url as provided"
    },
    ...
]}"""

In [8]:
user_prompt = """Respond with the most promising 5 deals from this list, selecting those which have the most detailed, high quality product description and a clear price.
Respond strictly in JSON, and only JSON. You should rephrase the description to be a summary of the product itself, not the terms of the deal.
Remember to respond with a paragraph of text in the product_description field for each of the 5 items that you select.
Be careful with products that are described as "$XXX off" or "reduced by $XXX" - this isn't the actual price of the product. Only respond with products when you are highly confident about the price. 

Deals:

"""
user_prompt += '\n\n'.join([deal.describe() for deal in deals])

In [9]:
print(user_prompt[:2000])

Respond with the most promising 5 deals from this list, selecting those which have the most detailed, high quality product description and a clear price.
Respond strictly in JSON, and only JSON. You should rephrase the description to be a summary of the product itself, not the terms of the deal.
Remember to respond with a paragraph of text in the product_description field for each of the 5 items that you select.
Be careful with products that are described as "$XXX off" or "reduced by $XXX" - this isn't the actual price of the product. Only respond with products when you are highly confident about the price. 

Deals:

Title: Samsung S90F 77" 4K OLED Vision AI Smart TV: Up to $400 off + free shipping
Details: Save at least $100 and as much as $400 on these three sizes. The deals:48" for $1,399.99 ($100 off)77" for $3,299.99 ($200 off)83" for $4,999.99 ($400 off) Shop Now at Samsung
Features: 
URL: https://www.dealnews.com/Samsung-S90-F-77-4-K-OLED-Vision-AI-Smart-TV-Up-to-400-off-free-sh

In [34]:
def get_recommendations():
    completion = groq_client.chat.completions.create(
        model="meta-llama/llama-4-scout-17b-16e-instruct",
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": user_prompt}
        ],
        temperature=0.0,
        max_tokens=2048
    )

    content = completion.choices[0].message.content

    # Strip Markdown code block markers
    if content.startswith("```"):
        content = content.strip("```").strip("json").strip()

    # Now parse the cleaned content
    try:
        result = json.loads(content)
        return DealSelection(**result)
    except json.JSONDecodeError as e:
        print("⚠️ Failed to parse JSON:", e)
        print("🔎 Raw content:", content)
        return None

In [35]:
result = get_recommendations()

In [36]:
len(result.deals)

5

In [37]:
result.deals[1]

Deal(product_description='The Open-box Apple MacBook Air M3 13" Laptop (2024) features a 13.6" Liquid Retina Display, Apple M3 8-Core CPU w/ 10-Core GPU, 16GB Unified Memory, and 256GB SSD. This model is identified as MC8K4LL/A and is a great option for those looking for a high-performance laptop.', price=722.0, url='https://www.dealnews.com/products/Apple/Apple-Mac-Book-Air-M3-13-Laptop-2024-w-16-GB-RAM-256-GB-SSD/484646.html?iref=rss-c39')

In [40]:
from agents.scanner_agent import ScannerAgent

In [41]:
agent = ScannerAgent()
result = agent.scan()

In [42]:
result

DealSelection(deals=[Deal(product_description='The Dell Inspiron 16 Plus 7640 is a laptop featuring a 16-inch 1920x1200 IPS touchscreen, Intel Core Ultra 9 185H 2.3GHz Meteor Lake H 16-core CPU, 16GB RAM, and 512GB NVMe M.2 SSD. It runs on Windows 11 Pro.', price=900.0, url='https://www.dealnews.com/Dell-Inspiron-16-Plus-7640-Core-Ultra-9-185-H-16-Touch-Laptop-for-900-free-shipping/21740394.html?iref=rss-c142'), Deal(product_description='The Dell Tower ECT1250 Core Ultra 7 265 Desktop PC features an Intel Core Ultra 7 265 20-Core 1.8GHz to 5.3GHz CPU, 16GB RAM, and 512GB NVMe M.2 SSD. It comes with a wired keyboard and mouse and runs on Windows 11 Pro.', price=700.0, url='https://www.dealnews.com/Dell-Tower-ECT1250-Core-Ultra-7-265-Desktop-PC-for-700-free-shipping/21740397.html?iref=rss-c142'), Deal(product_description='The Open-box Apple MacBook Air M3 13" Laptop (2024) features a 13.6" Liquid Retina Display, Apple M3 8-Core CPU w/ 10-Core GPU, 16GB Unified Memory, and 256GB SSD. The 